In [2]:
import nglview as nv    # Импортируем библиотеку
import requests         # Этот стандартный модуль позволяет посылать запросы к веб-ресурсам
import json             # Этот стандартный модуль позволяет легко работать с текстовым форматом json

my_query = {
    "query": {
        "type": "group",
        "logical_operator": "and",
        "nodes": []
    },
    "return_type": "entry"
}



example_field_search = {
    "type": "terminal",
    "service": "text", # Сервис поиска в определенном поле записи
    "parameters": {
        "value": "estrogen",        # Название моего белка
        "attribute": "struct.title", # В данном случае это поле -- заголовок записи
        "operator": "contains_words" # Должны присутствовать какие-то слова 
                                     # из запроса, но не обязательно все
    }
}

my_query["query"]["nodes"].append(example_field_search)

# Какое разрешение: не хуже 2.6 ангстрем

resolution_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.6,
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

my_query["query"]["nodes"].append(resolution_clause)

# Сколько лигандов должно быть в записи: не меньше 1 (то есть больше 0)

has_ligand_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 0,
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

# Дата публикации записи: с 1 января 2015 по 1 января 2020 года

date_range_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2015-01-01", # год-месяц-день
            "to": "2020-01-01",
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)

# Префикс адреса, по которому нужно отослать запрос. 
# Сам запрос должен быть сформирован в виде строки и подан аргументу data

rcsb = 'https://search.rcsb.org/rcsbsearch/v1/query'

json_query = json.dumps(my_query) # Функция dumps буквально значит "dump string", 
                                  # то есть превращает словарь в строку 
                                  # с правильным форматированием

search = requests.post(f'{rcsb}', data=json_query) # Отсылаем запрос

search_result = search.json() # Распаковываем ответ сервера в словарь
search_result

best_hit = search_result["result_set"][0] # Лучшая находка
best_hit

{'identifier': '6SBO',
 'score': 1.0,
 'services': [{'service_type': 'text',
   'nodes': [{'node_id': 29512,
     'original_score': 185.5599365234375,
     'norm_score': 1.0}]}]}

In [ ]:
Мы получили 6SBO - Estrogen receptor mutant L536S, она соответствует всем требованиям заданным для поиска.

Какое отношение она имеет к ключевым словам запроса? Какова роль молекулы из запроса в жизни остальных молекул из записи?

Более 75% случаев рака молочной железы являются положительными к альфа-рецептору эстрогена (ERa) (ER+),s
и резистентность к современной гормональной терапии возникает у трети пациентов с ER+.
Устойчивость опухоли по-прежнему зависит от ERa, но мутации обычно приводят к конститутивной активации рецептора гормона,
что делает неэффективными препараты-модуляторы ERa, такие как тамоксифен и ингибиторы ароматазы.
Фульвестрант является мощным селективным разрушителем рецепторов эстрогена (SERD),
который разрушает рецептор ERa в опухолях, устойчивых к лекарственным средствам,
и был одобрен для лечения метастатического рака молочной железы с положительным гормональным рецептором после антиэстрогенной терапии.

In [3]:
from ipywidgets import interact, fixed

my_examples = {
    'Example 1': {
        'description': '''
Белок в виде cartoon, покраска по типу вторичной структуры
Боковые радикалы покрашены по элементу, показаны линиями
Боковые радикалы ароматических аминокислот показаны в стержневой модели
Лиганды показаны в виде Ван-дер-Ваальсовых сфер, покрашены по гидрофобности
''',
        'representations': [
            {
                'type': 'spacefill',                      
                'params': {
                    'sele': 'ligand',                     
                    'color': 'hydrophobicity' 
                 }
            },
            {
                'type': 'line',                      
                'params': {
                    'sele': 'sidechainAttached',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'sstruc'
                 }
            },
            {
                'type': 'licorice',                      
                'params': { 
                    'sele': 'aromatic',                     
                    'color': 'element'  
                }
            },
        ],
    },
    'Example 2': {
        'description': '''
Белок в виде cartoon темно-серого цвета
Боковые радикалы в виде линий светло-серого цвета
Боковые радикалы полярных аминокислот в виде hyperball, покрашены по элементам
Лиганды в шаростержневой модели, покрашены по элементам, углероды покрашены в темно-синий
''',
        'representations': [
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',               
                    'color': 'darkgray'  
                 }
            },
            {
                'type': 'hyperball',                      
                'params': {
                    'sele': 'polar',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'line',                      
                'params': {
                    'sele': 'sidechainAttached',                     
                    'color': 'lightgray'  
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand',                     
                    'color': 'element'  
                 }
            },
            
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand and _C',                     
                    'color': 'darkblue'  
                 }
            },
        ],
    },
    'Example 3': {
        'description': '''
Белок в виде ribbon, покрашенной градиентом от N к C концу
Боковые радикалы в стержневой модели, покрашенные по элементам
Углероды гидрофобных аминокислот покрашены в светло-желтый
Углероды полярных заряженных аминокислот покрашены в светло-голубой
Лиганды не показаны никак
''',
        'representations': [
            {
                'type': 'ribbon',                      
                'params': {
                    'sele': 'all',               
                    'color': 'residueindex'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'hydrophobic and _C',                     
                    'color': 'lightyellow'  
                 }
            },
            {
                'type': 'line',                      
                'params': {
                    'sele': 'polar and charged and _C',                     
                    'color': 'LightBlue'  
                 }
            },
           
        ],
    },
}
def show_examples(view, example_name):
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("6SBO", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Example 1', 'Example 2', 'Example 3'), va…

NGLWidget()